# BPT Example Usage

## 0. Summary

### A. Description
  1. **Case 1:** General data I/O with a custom `bpt.py` script
  2. **Case 2:** Data joins with star rating
  3. **Case 3:** Case Study: Mapping Projection Assumptions onto Choropleth Map

### B. Where Can I Access Publicly-Available BPT datasets? 
Historical BPT data from 2006-2018 can be downloaded in the CMS website under [Medicare/Medicare Advantage Rates & Statistics/Data](https://www.cms.gov/Medicare/Health-Plans/MedicareAdvtgSpecRateStats/DataFiles). For each year 2014 and after, the bid data is standardized and includes the following zip files:
  * CY20XX MA Pricing Data Release Technical Notes (PDF)
  * Dictionary
  * MA data
  * ESRD data
  * MSA data

Data in earlier years store the data corresponding to each workbook as individual zip files. The functions in `bpt.py` should be able to preprocess those.

### C. The MA datasets
Within the MA zip file, there are serveral tab delimited text files with the prefix `ma_X`, where `X` is a number corresponding to a worksheet in the BPT workbook. Each number corresponds to the following fields:
  * `ma_1`: Base Period Experience and Projection Assumptions
  * `ma_2`: MA Projected Allowed Costs PMPM
  * `ma_3`: MA Projected Cost Sharing PMPM
  * `ma_4`: MA Projected Revenue Requirement PMPM
  * `ma_5_cnty_obsXXXXXX_XXXXXX_20XX`: MA Benchmark PMPM by county, observations, and year
  * `ma_6`: MA Bid Summary
  * `ma_7`: Optional Supplemental Benefits

## 1. BPT Data Loading and Preprocessing

### A. Motivation
There are several files that are required to analyze the bid data in its full context. The `bpt.py` module enables the user to access the bid data more easily, where all `*.zip` files  in a single directory. The goal of the module was to save time on I/O to conduct faster data analyses.

### B. Data directory structure
To use this library out of the box, it is suggested that BPT data directory structure should be as followed:

```
data/
  |- 20XX/
       |- BPT20XX_ma_0.zip
```

### C. BPT usage

The BPT class takes in a single paramter `dir_to_query:str`, which is a directory that can contain multiple objects. 

Below are the main operations and the associated functions in the python script:

  1. `load_data_dict(dirpath: str) -> pd.DataFrame`: Function that reads in the data dictionary containing human-readable field names and return a dataframe that maps the headers for each text file (`ma_X`) to the human-readable field.
  2. `load_sheet(dirpath: str, objname:str) -> pd.DataFrame`: Function that loads the zipped text files into pandas Dataframes.
  3. `load_county_data(dirpath: str, objname:str="ma_5") -> pd.DataFrame`: Function that reads in the benchmark data, which consists of the several text files with the `ma_5_...` prefix, as a single pandas dataframe.
  4. `replace_field_to_name(meta: pd.DataFrame, df: pd.DataFrame) -> pd.DataFrame`: Function that replaces the column headers (excel column locations) to human-readable column names.
  5. `BPT`: A class corresponding to a given year for the BPT data. Contains the year, meta data, and each workbook with the structure `ma_X`. Note that entries without a Bid ID are dropped.

### D. Example: Loading 2015 BPT data
Let's load up the 2015 BPT data as an example.

In [25]:
from bpt import BPT
import pandas as pd
import numpy as np

In [2]:
dir_to_query = '/mnt/c/Users/ScottCampit_nzmndyg/Projects/bid-pricing-tool/data/2015/'
BPT2015 = BPT(dir_to_query)

LOADING 2015 BPT DATA
LOADING BASE PERIOD EXPERIENCE ('ma_1') DATA
LOADING PROJECTED ALLOWED COST ('ma_2') DATA
LOADING PROJECTED COST SHARING ('ma_3') DATA
LOADING PROJECTED REV REQUIREMENT ('ma_4') DATA
LOADING BENCHMARK ('ma_5') DATA
LOADING BID SUMMARY ('ma_6') DATA
LOADING OPTIONAL SUPPLEMENTAL BENEFITS ('ma_7') DATA


To view MA Bid Summary data (stored in `ma_6`), call the object in the BPT class. This will return a pandas dataframe that can be further refined (e.g. fillnas, ensure datatypes are correct, etc.)

In [3]:
pd.set_option('display.max_columns', None)
bid_summary = BPT2015.ma_6
bid_summary

BID ID (H-number, Plan ID, Segment ID)  Contract Year (2015)  \
0                               H0028_001_0                  2015   
1                               H0028_002_0                  2015   
2                               H0028_003_0                  2015   
3                               H0028_004_0                  2015   
4                               H0028_801_0                  2015   
...                                     ...                   ...   
3541                            R7444_001_0                  2015   
3542                            R9896_008_0                  2015   
3543                            R9896_009_0                  2015   
3544                            R9896_012_0                  2015   
3545                            R9896_021_0                  2015   

      Version Number Medicare-covered Net medical cost( MA Bid Summary!D0025)  \
0                  3                                           473.2208         
1                  3                                           537.4973         
2                  3                                                  *         
3                  3                                           448.1032         
4                  3                                           520.2695         
...              ...                                                ...         
3541               2                                           613.9036         
3542               4                                          1208.7383         
3543               5                                            826.765         
3544               5                                           516.5867         
3545               4                                           818.5822         

      Medicare-covered Non-medical expense( MA Bid Summary!D0027)  \
0                                              103.6732             
1                                              104.6150             
2                                              101.4875             
3                                               87.0015             
4                                               63.3785             
...                                                 ...             
3541                                            89.7746             
3542                                           125.8367             
3543                                           109.0657             
3544                                            87.6878             
3545                                           111.2960             

     Medicare-covered Gain / loss margin( MA Bid Summary!D0028)  \
0                                          -15.27038499           
1                                          -48.05239067           
2                                                     *           
3                                          -26.16840231           
4                                          -22.98709543           
...                                                 ...           
3541                                        60.71346891           
3542                                        268.6700061           
3543                                        93.08431431           
3544                                        60.48050404           
3545                                        26.37684447           

      Total Medicare-covered revenue requirement( MA Bid Summary!D0029)  \
0                                              561.6236                   
1                                              594.0599                   
2                                              711.8527                   
3                                              508.9363                   
4                                              560.6609                   
...                                                 ...                   
3541                                        

Let's now get columns with cost sharing information.

In [4]:
cost_share_2015 = bid_summary.filter(like='Shar')
cost_share_2015

PMPM Medical Allocation to Reduce A/B Cost Share( MA Bid Summary!I0025)  \
0                                               18.9921                        
1                                               20.5748                        
2                                                     *                        
3                                               50.1252                        
4                                               18.6427                        
...                                                 ...                        
3541                                             5.8628                        
3542                                             7.7278                        
3543                                            19.6945                        
3544                                             12.426                        
3545                                             1.1728                        

      PMPM Admin Allocation to Reduce A/B Cost Share( MA Bid Summary!J0025)  \
0                                                4.1608                       
1                                                4.0046                       
2                                                0.8925                       
3                                                9.7321                       
4                                                2.2710                       
...                                                 ...                       
3541                                             0.8574                       
3542                                             0.8045                       
3543                                             2.5981                       
3544                                             2.1092                       
3545                                             0.1595                       

     Reduce A/B Cost Share - PMPM Allocation Gain/Loss( MA Bid Summary!K0025)  \
0                                               -0.6129                         
1                                               -1.8394                         
2                                                     *                         
3                                               -2.9272                         
4                                               -0.8237                         
...                                                 ...                         
3541                                             0.5798                         
3542                                             1.7177                         
3543                                             2.2174                         
3544                                             1.4548                         
3545                                             0.0378                         

      Total PMPM Allocation to Reduce A/B Cost Share( MA Bid Summary!L0025)  \
0                                                 22.54                       
1                                                 22.74                       
2                                                  6.26                       
3                                                 56.93                       
4                                                 20.09                       
...                                                 ...                       
3541                                               7.30                       
3542                                              10.25                       
3543                                              24.51                       
3544                                              15.99                       
3545                                               1.37                       

      Max Value for Reduce A/B Cost Share( MA Bid Summary!M0025)  \
0                                                 22.54            
1                                    

### E. Example: Data Cleaning
We can do some data quality checks and data cleaning. 

For the following example, we will examine the BPT projection assumptions or projection factor. These projection factors are values that are used to project the base period data to the contract period.
  * There are projection assumptions for each of the 18 service category (e.g. Inpatient facility, Skilled Nursing Facility, etc).  
  * Additionally, there are 3 categories of projection assumptions: Util/1000, Unit Cost, and Additive Adjustments
  * Together, the service category + projection assumption categories make up the columns while the rows consist of the bid ids.

#### Expected data range
The expected values should be a positive floating point value. None of the entries *should* be zero (but surprisingly, there are, and there's no documentation why that is!)


#### Missing values
For instance, there are asterisks in some of the row entries. Per the 2015 Bid Pricing Tool Technical Notes:

*"Any information that could be used to identify Medicare beneficiaries or other individuals. As 
part of this exclusion, an \[asterisk\] indicates that a data field has been suppressed because there are 
fewer than 11 Medicare beneficiaries in the data field or for necessary complimentary cell 
suppression."*

Additionally, there are entries where there is no entry at all, and thus the cell contains NaNs. 

#### What we'll do:
  1. Get the projection assumptions
  2. Set zeros to ones and fill in missing values with 1
  3. Separate out the projection assumptions by category (Util/1000, Unit Cost, Additive)

In [12]:
base_period = BPT2015.ma_1

First, get projection assumptions.

In [18]:
prj_asmpt_pattern = "BID ID|MA Base!J00(2[7-9]|3[0-9]|4[0-4])|MA Base!K00(2[7-9]|3[0-9]|4[0-4])|MA Base!L00(2[7-9]|3[0-9]|4[0-4])|MA Base!M00(2[7-9]|3[0-9]|4[0-4])|MA Base!N00(2[7-9]|3[0-9]|4[0-4])|MA Base!O00(2[7-9]|3[0-9]|4[0-4])|MA Base!P00(2[7-9]|3[0-9]|4[0-4])|MA Base!Q00(2[7-9]|3[0-9]|4[0-4])"
prj_asmpt = base_period.loc[:, base_period.columns.str.contains(pat=prj_asmpt_pattern, regex=True)]
prj_asmpt = prj_asmpt.set_index('BID ID (H-number, Plan ID, Segment ID)')
prj_asmpt.head(3)

/tmp/ipykernel_3832/4245737771.py:2: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  prj_asmpt = base_period.loc[:, base_period.columns.str.contains(pat=prj_asmpt_pattern, regex=True)]


Inpatient Facility [Util/1000 Trend]( MA Base!J0027)  \
BID ID (H-number, Plan ID, Segment ID)                                                         
H0028_001_0                                                                      1.041586      
H0028_002_0                                                                      1.048467      
H0028_003_0                                                                      1.035891      

                                        Skilled Nursing Facility [Util/1000 Trend]( MA Base!J0028)  \
BID ID (H-number, Plan ID, Segment ID)                                                               
H0028_001_0                                                                      1.040309            
H0028_002_0                                                                      1.033212            
H0028_003_0                                                                      1.045731            

                                        Home Health [Util/1000 Trend]( MA Base!J0029)  \
BID ID (H-number, Plan ID, Segment ID)                                                  
H0028_001_0                                                                  1.085316   
H0028_002_0                                                                  1.110564   
H0028_003_0                                                                  1.096176   

                                        Ambulance [Util/1000 Trend]( MA Base!J0030)  \
BID ID (H-number, Plan ID, Segment ID)                                                
H0028_001_0                                                                1.085316   
H0028_002_0                                                                1.110564   
H0028_003_0                                                                1.096176   

                                        DME/Prosthetics/Supplies [Util/1000 Trend]( MA Base!J0031)  \
BID ID (H-number, Plan ID, Segment ID)                                                               
H0028_001_0                                                                      1.085316            
H0028_002_0                                                                      1.110564            
H0028_003_0                                                                      1.096176            

                                        OP Facility - Emergency [Util/1000 Trend]( MA Base!J0032)  \
BID ID (H-number, Plan ID, Segment ID)                                                              
H0028_001_0                                                                      1.064892           
H0028_002_0                                                                      1.078348           
H0028_003_0                                                                      1.068046           

                                        OP Facility - Surgery [Util/1000 Trend]( MA Base!J0033)  \
BID ID (H-number, Plan ID, Segment ID)                                                            
H0028_001_0                                                                      1.058333         
H0028_002_0                                                                      1.068757         
H0028_003_0                                                                      1.064381         

                                        OP Facility - Other [Util/1000 Trend]( MA Base!J0034)  \
BID ID (H-number, Plan ID, Segment ID)                                                          
H0028_001_0                                                                      1.062038       
H0028_002_0                                                                      1.072278       
H0028_003_0                                                                      1.065199       

                                        Professional [Util/1000 Trend]( MA Base!J0035)  \
BID ID (H-number, Plan ID, Segment ID)                                       

Replace missing values.

In [27]:
prj_asmpt = prj_asmpt.replace('*', 1)
prj_asmpt = prj_asmpt.replace(np.nan, 1)
prj_asmpt = prj_asmpt.replace(0, 1)
prj_asmpt = prj_asmpt.apply(lambda x: pd.to_numeric(x), axis=1, errors='coerce')
prj_asmpt.head(3)

Inpatient Facility [Util/1000 Trend]( MA Base!J0027)  \
BID ID (H-number, Plan ID, Segment ID)                                                         
H0028_001_0                                                                      1.041586      
H0028_002_0                                                                      1.048467      
H0028_003_0                                                                      1.035891      

                                        Skilled Nursing Facility [Util/1000 Trend]( MA Base!J0028)  \
BID ID (H-number, Plan ID, Segment ID)                                                               
H0028_001_0                                                                      1.040309            
H0028_002_0                                                                      1.033212            
H0028_003_0                                                                      1.045731            

                                        Home Health [Util/1000 Trend]( MA Base!J0029)  \
BID ID (H-number, Plan ID, Segment ID)                                                  
H0028_001_0                                                                  1.085316   
H0028_002_0                                                                  1.110564   
H0028_003_0                                                                  1.096176   

                                        Ambulance [Util/1000 Trend]( MA Base!J0030)  \
BID ID (H-number, Plan ID, Segment ID)                                                
H0028_001_0                                                                1.085316   
H0028_002_0                                                                1.110564   
H0028_003_0                                                                1.096176   

                                        DME/Prosthetics/Supplies [Util/1000 Trend]( MA Base!J0031)  \
BID ID (H-number, Plan ID, Segment ID)                                                               
H0028_001_0                                                                      1.085316            
H0028_002_0                                                                      1.110564            
H0028_003_0                                                                      1.096176            

                                        OP Facility - Emergency [Util/1000 Trend]( MA Base!J0032)  \
BID ID (H-number, Plan ID, Segment ID)                                                              
H0028_001_0                                                                      1.064892           
H0028_002_0                                                                      1.078348           
H0028_003_0                                                                      1.068046           

                                        OP Facility - Surgery [Util/1000 Trend]( MA Base!J0033)  \
BID ID (H-number, Plan ID, Segment ID)                                                            
H0028_001_0                                                                      1.058333         
H0028_002_0                                                                      1.068757         
H0028_003_0                                                                      1.064381         

                                        OP Facility - Other [Util/1000 Trend]( MA Base!J0034)  \
BID ID (H-number, Plan ID, Segment ID)                                                          
H0028_001_0                                                                      1.062038       
H0028_002_0                                                                      1.072278       
H0028_003_0                                                                      1.065199       

                                        Professional [Util/1000 Trend]( MA Base!J0035)  \
BID ID (H-number, Plan ID, Segment ID)                                       

Separate projection assumptions by category.

In [28]:
util_adj = prj_asmpt.filter(regex=('Util/1000 Trend|Benefit Plan Change|Population Change|/[Other Factor/]'), axis=1)
unitcost_adj = prj_asmpt.filter(regex='Unit Cost')
additive_adj = prj_asmpt.filter(regex='Additive Adjustment')

In [29]:
additive_adj.head(3)

Inpatient Facility [Additive Adjustment Util/1000]( MA Base!P0027)  \
BID ID (H-number, Plan ID, Segment ID)                                                                       
H0028_001_0                                                                           1.0                    
H0028_002_0                                                                           1.0                    
H0028_003_0                                                                           1.0                    

                                        Skilled Nursing Facility [Additive Adjustment Util/1000]( MA Base!P0028)  \
BID ID (H-number, Plan ID, Segment ID)                                                                             
H0028_001_0                                                                           1.0                          
H0028_002_0                                                                           1.0                          
H0028_003_0                                                                           1.0                          

                                        Home Health [Additive Adjustment Util/1000]( MA Base!P0029)  \
BID ID (H-number, Plan ID, Segment ID)                                                                
H0028_001_0                                                                           1.0             
H0028_002_0                                                                           1.0             
H0028_003_0                                                                           1.0             

                                        Ambulance [Additive Adjustment Util/1000]( MA Base!P0030)  \
BID ID (H-number, Plan ID, Segment ID)                                                              
H0028_001_0                                                                           1.0           
H0028_002_0                                                                           1.0           
H0028_003_0                                                                           1.0           

                                        DME/Prosthetics/Supplies [Additive Adjustment Util/1000]( MA Base!P0031)  \
BID ID (H-number, Plan ID, Segment ID)                                                                             
H0028_001_0                                                                           1.0                          
H0028_002_0                                                                           1.0                          
H0028_003_0                                                                           1.0                          

                                        OP Facility - Emergency [Additive Adjustment Util/1000]( MA Base!P0032)  \
BID ID (H-number, Plan ID, Segment ID)                                                                            
H0028_001_0                                                                           1.0                         
H0028_002_0                                                                           1.0                         
H0028_003_0                                                                           1.0                         

                                        OP Facility - Surgery [Additive Adjustment Util/1000]( MA Base!P0033)  \
BID ID (H-number, Plan ID, Segment ID)                                                                          
H0028_001_0                                                                           1.0                       
H0028_002_0                                                                           1.0                       
H0028_003_0                                                                           1.0                       

                                        OP Facility - Other [Additive Adjustment Util/1000]( MA Base!P0034)  \
BID ID (H-number, Plan ID, Segment ID)              

## 2. Data Joins with Star Rating Data

If we wanted to, we can merge the bid data with other data sources such as Star Rating using the BID ID number. We'll demonstrate how to do that with the 2015 BPT data loaded above.

First, let's load the 2015 Star Rating data, which can be found [here](https://www.cms.gov/medicare/prescription-drug-coverage/prescriptiondrugcovgenin/performancedata)
  * Folder name: `2015_Star_Ratings_and_Display_Measures.zip`
  * File of interest: `2015 Star Ratings Fall Release (10_2014)/2015_Report_Card_Master_Table_2014_10_03_summary.csv`

The functions below scrape Star Rating data from the CMS website.

In [34]:
import os
import requests
import zipfile
import io
from bs4 import BeautifulSoup as bs

BASEURL = 'https://www.cms.gov/'

def check_if_file_exists(url:str=None, data_directory:str=None, save_file:bool=True):
    """
    Automatically checks whether or not the queried data is stored locally in the machine. 
        * If there is a record, then the file will not be saved.
        * Otherwise, the file will be saved at the directory specified.

    Note: if a directory is not supplied, the file will NOT be saved.
    """
    if None not in (data_directory, url, save_file):
        datastore = os.listdir(data_directory)
        if url.split('/')[-1] not in datastore:
            r = requests.get(url)
            filename = url.split('/')[-1]
            with open(data_directory+filename, 'wb') as file_:
                file_.write(r.content)
        else:
            return

def get_star_rating(
        STARPATH:str="Medicare/Prescription-Drug-Coverage/PrescriptionDrugCovGenIn/PerformanceData", \
        SAVE_PATH:str=None,#Example: "C:/Users/ScottCampit/Projects/quadrant-chart/data/", \
        year:str=None
    ):
    """Scrapes Star Rating data from the CMS website."""
    r = requests.get(BASEURL+STARPATH)
    soup = bs(r.text, 'html.parser')
    all_data_urls = list()
    for name in soup.findAll('a', href=True):
        zipurl = name['href']
        if zipurl.endswith('.zip'):
            if any(filename in zipurl for filename in ('data', 'Data')):
                if year:
                    if any(filename in zipurl for filename in (year)):
                        all_data_urls.append(zipurl)
                else:
                    all_data_urls.append(zipurl)
            
    # Get the latest zip file containing the star rating data.
    latest_arxiv = all_data_urls[0]
    new_r2 = requests.get(BASEURL+latest_arxiv)
    check_if_file_exists(url=BASEURL+latest_arxiv, data_directory=SAVE_PATH)

    arxiv = zipfile.ZipFile(io.BytesIO(new_r2.content), 'r')
    for name in arxiv.namelist():
        if 'Summary' in name: # The relevant .csv file we need
            df = pd.read_csv(arxiv.open(name), skiprows=1)
            df = df.dropna(axis=1, how='all')
    
    return df

In [55]:
star2015 = get_star_rating(SAVE_PATH=None, year='2015')
star2015.head(3)

Contract Number                         Organization Type  \
0          E3014   Employer/Union Only Direct Contract PDP    
1          E4744   Employer/Union Only Direct Contract PDP    
2          H0022                                      Demo    

                                 Contract Name  \
0                           PSERS HOP PROGRAM    
1  MODOT/MSHP MEDICAL AND LIFE INSURANCE PLAN    
2         BUCKEYE COMMUNITY HEALTH PLAN, INC.    

                         Organization Marketing Name  \
0  Pennsylvania Public School Employees Retiremen...   
1             MISSOURI DEPARTMENT OF TRANSPORTATION    
2                 Buckeye Health Plan - MyCare Ohio    

                                 Parent Organization  SNP  2020 Disaster %  \
0  Commonwealth of PA Pub Schools Retirement System   No             100.0   
1   Missouri Highways and Transportation Commission   No             100.0   
2                               Centene Corporation   No             100.0   

   2021 Disaster % 2023 Part C Summary         2023 Part D Summary  \
0                1     Not Applicable                          4.5   
1                1     Not Applicable                          3.5   
2                0     Not Applicable   Not enough data available    

                2023 Overall  
0             Not Applicable  
1             Not Applicable  
2  Not enough data available

We can map Star Rating data by Contract Number to the bid ID. Unfortunately, we don't have higher resolution with the segment IDs.

In [56]:
star2015['Contract Number'] = star2015['Contract Number'].str.rstrip()

In [59]:
prj_asmpt['Contract ID'] = prj_asmpt.index.str.split(pat='_', n=1).str[0]
joined_prj_asmpt = pd.merge(star2015, prj_asmpt, how='inner', left_on='Contract Number', right_on='Contract ID')
joined_prj_asmpt = joined_prj_asmpt.drop(['Contract ID'], axis=1)
joined_prj_asmpt.head(3)

Contract Number Organization Type   Contract Name  \
0           H0028        Local CCP   CHA HMO, INC.    
1           H0028        Local CCP   CHA HMO, INC.    
2           H0028        Local CCP   CHA HMO, INC.    

  Organization Marketing Name Parent Organization   SNP  2020 Disaster %  \
0                     Humana         Humana Inc.   Yes             100.0   
1                     Humana         Humana Inc.   Yes             100.0   
2                     Humana         Humana Inc.   Yes             100.0   

   2021 Disaster % 2023 Part C Summary 2023 Part D Summary 2023 Overall  \
0               41                   4                   4            4   
1               41                   4                   4            4   
2               41                   4                   4            4   

   Inpatient Facility [Util/1000 Trend]( MA Base!J0027)  \
0                                           1.041586      
1                                           1.048467      
2                                           1.035891      

   Skilled Nursing Facility [Util/1000 Trend]( MA Base!J0028)  \
0                                           1.040309            
1                                           1.033212            
2                                           1.045731            

   Home Health [Util/1000 Trend]( MA Base!J0029)  \
0                                       1.085316   
1                                       1.110564   
2                                       1.096176   

   Ambulance [Util/1000 Trend]( MA Base!J0030)  \
0                                     1.085316   
1                                     1.110564   
2                                     1.096176   

   DME/Prosthetics/Supplies [Util/1000 Trend]( MA Base!J0031)  \
0                                           1.085316            
1                                           1.110564            
2                                           1.096176            

   OP Facility - Emergency [Util/1000 Trend]( MA Base!J0032)  \
0                                           1.064892           
1                                           1.078348           
2                                           1.068046           

   OP Facility - Surgery [Util/1000 Trend]( MA Base!J0033)  \
0                                           1.058333         
1                                           1.068757         
2                                           1.064381         

   OP Facility - Other [Util/1000 Trend]( MA Base!J0034)  \
0                                           1.062038       
1                                           1.072278       
2                                           1.065199       

   Professional [Util/1000 Trend]( MA Base!J0035)  \
0                                        1.034823   
1                                        1.039763   
2                                        1.049049   

   Part B Rx [Util/1000 Trend]( MA Base!J0036)  \
0                                     1.038227   
1                                     1.051768   
2                                     1.062640   

   Other Medicare Covered [Util/1000 Trend]( MA Base!J0037)  \
0                                                1.0          
1                                                1.0          
2                                                1.0          

   Transportation (Non-Covered) [Util/1000 Trend]( MA Base!J0038)  \
0                                                1.0                
1                                                1.0                
2                                                1.0                

   Dental (Non-Covered) [Util/1000 Trend]( MA Base!J0039)  \
0                                                1.0        
1                                                1.0        
2                                                1.0        

   Vision (Non-Covered) [Util/1000 Trend]( MA Base!J0040)  \
0        

## 3. Case Study: Mapping Projection Assumptions onto Choropleth Map

This case-study examines the projection assumptions at the county-level. 

Note that there are several steps to map the data to FIPs. We took this approach:
  1. Load the benchmark data (`ma_5`), which contains a mapping of the Bid IDs -> county.
  2. Load a county-FIPs mapping obtained [here](https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json).
  3. Merge the two sources.
  4. Extract the projection assumptions from `ma_1` using the mapped Bid ID <-> FIPs relationship.
  5. Look at specific projection assumptions that had high variance across plans.

The resulting dataframe is the `chloropleth_outliers.csv`, which contains the top 10 service categories for each projection assumption that had the highest variance across all bid IDs.

First, load the FIPs-mapped data.

In [67]:
from urllib.request import urlopen
import requests
import json
from sklearn.preprocessing import MinMaxScaler

# Specialized libraries for geographic analysis
import geopandas as gpd
import branca.colormap as cm
import folium
import branca

In [68]:
county_path = "/mnt/c/users/ScottCampit_nzmndyg/Projects/bid-pricing-tool/analysis/2015/chloropleth_outliers.csv"
county_df = pd.read_csv(county_path)
county_df.head(3)

/tmp/ipykernel_3832/1366550535.py:2: DtypeWarning: Columns (239,240,241,242,264,291,292,293,294,345) have mixed types. Specify dtype option on import or set low_memory=False.
  county_df = pd.read_csv(county_path)


Inpatient Facility Utilizers( MA Base!C0027)  \
0                                        4754.0   
1                                        4754.0   
2                                        4754.0   

   Skilled Nursing Facility Utilizers( MA Base!C0028)  \
0                                              919.0    
1                                              919.0    
2                                              919.0    

   Home Health Utilizers( MA Base!C0029)  Ambulance Utilizers( MA Base!C0030)  \
0                                 2670.0                               3548.0   
1                                 2670.0                               3548.0   
2                                 2670.0                               3548.0   

   DME/Prosthetics/Supplies Utilizers( MA Base!C0031)  \
0                                            12303.0    
1                                            12303.0    
2                                            12303.0    

   OP Facility - Emergency Utilizers( MA Base!C0032)  \
0                                             6726.0   
1                                             6726.0   
2                                             6726.0   

   OP Facility - Surgery Utilizers( MA Base!C0033)  \
0                                           2140.0   
1                                           2140.0   
2                                           2140.0   

   OP Facility - Other Utilizers( MA Base!C0034)  \
0                                        24508.0   
1                                        24508.0   
2                                        24508.0   

   Professional Utilizers( MA Base!C0035)  \
0                                 25404.0   
1                                 25404.0   
2                                 25404.0   

   Part B Rx Utilizers( MA Base!C0036)  \
0                              11604.0   
1                              11604.0   
2                              11604.0   

   Other Medicare Covered Utilizers( MA Base!C0037)  \
0                                           10165.0   
1                                           10165.0   
2                                           10165.0   

   Transportation (Non-Covered) Utilizers( MA Base!C0038)  \
0                                              721.0        
1                                              721.0        
2                                              721.0        

   Dental (Non-Covered) Utilizers( MA Base!C0039)  \
0                                             0.0   
1                                             0.0   
2                                             0.0   

   Vision (Non-Covered) Utilizers( MA Base!C0040)  \
0                                          4269.0   
1                                          4269.0   
2                                          4269.0   

   Hearing (Non-Covered) Utilizers( MA Base!C0041)  \
0                                             53.0   
1                                             53.0   
2                                             53.0   

   Health & Education Utilizers( MA Base!C0042)  \
0                                         715.0   
1                                         715.0   
2                                         715.0   

   Other Non-Covered Utilizers( MA Base!C0043)  \
0                                          0.0   
1                                          0.0   
2                                          0.0   

  Contract Number( MA Base!D0005)  Plan ID( MA Base!D0006)  \
0                           H0151                        1   
1                           H0151                        1   
2                           H0151                        1   

   Segment ID( MA Base!D0007)  Contract Year (MA Base!D0008)  \
0                           0                           2015   
1                           0                           2015   
2                           0                           20

To use the library folium, we need this JSON file that contains the coordinates of each county that can be mapped to... well, the U.S. map.

In [74]:
url = "https://raw.githubusercontent.com/python-visualization/folium/master/examples/data"
county_geo = f"{url}/us_counties_20m_topo.json"

geoJSON_df = gpd.read_file(county_geo)
geoJSON_df['id'] = geoJSON_df["id"].str[-5:].astype(int)
geoJSON_df.head(3)

id                                           geometry
0  1001  POLYGON ((-86.49932 32.34394, -86.71470 32.402...
1  1009  POLYGON ((-86.57112 33.76632, -86.75060 33.841...
2  1017  POLYGON ((-85.17117 32.86797, -85.13527 32.771...

We'll define some functions we need to filter and scale the dataset.

In [70]:
def filter_by_mco(df:pd.DataFrame, mco_type:str) -> pd.DataFrame:
    """Filter by plan type"""
    if mco_type != 'All':
        mco_df = df.loc[df['Plan Type( MA Base!G0007)'] == mco_type]
    else:
        mco_df = df
    return mco_df

def filter_by_org(df:pd.DataFrame, org:str) -> pd.DataFrame:
    """Filter by organization name"""
    if org != 'All':
        org_df = df.loc[df['Organization Name( MA Base!G0005)'] == org]
    else:
        org_df = df
    return org_df

def make_filtered_df(df:pd.DataFrame, mco_type:str, org:str) -> pd.DataFrame:
    """Wrap the filter by plan type and organization functions"""
    mco_df = filter_by_mco(df, mco_type)
    return filter_by_org(mco_df, org)

def filter_by_feat(df:pd.DataFrame, feat_of_interest:str) -> pd.DataFrame:
    """Filter by projection assumption"""
    return df.groupby("FIPS State county code")[feat_of_interest].mean()

def minmaxscale(df:pd.DataFrame) -> pd.DataFrame:
    """Performs min-max scaling across all data."""
    min_val = df.min()
    max_val = df.max()
    return (df - min_val) / (max_val - min_val)

def make_colorscale_df(df:pd.DataFrame, mco_type:str, org:str, feat_of_interest:str) -> pd.DataFrame:
    """Create a dataframe that will be used as the color scale."""
    mco_df = filter_by_mco(df, mco_type)
    org_df = filter_by_org(mco_df, org)
    feat_df = filter_by_feat(org_df, feat_of_interest)
    return minmaxscale(feat_df)

def create_overlay_data(geojson_df:pd.DataFrame, bpt_df:pd.DataFrame, feat_of_interest:str) -> pd.DataFrame:
    """Take the GeoJSON coordinates and the bid data, and perform a merge by FIPS"""

    tmp_df = bpt_df[['State 1( MA Bnchmk!C0039)', 
                    'County Name 1( MA Bnchmk!D0039)', 
                    'FIPS State county code', 
                    feat_of_interest]]

    tmp_df = tmp_df.groupby(['State 1( MA Bnchmk!C0039)', 
                    'County Name 1( MA Bnchmk!D0039)', 
                    'FIPS State county code'])[feat_of_interest].mean().reset_index()
    
    return pd.merge(geojson_df, tmp_df, 
                    how='inner', 
                    left_on='id', right_on='FIPS State county code')

colorscale = branca.colormap.linear.YlOrRd_09.scale()
def style_function(feature):
    """Note: color_df is declared outside of the function scope."""
    q = color_df.get(key=int(feature["id"][-5:]), default=None)
    return {
        "fillOpacity": 0.5,
        "weight": 0,
        "fillColor": "#black" if q is None else colorscale(q),
    }

def construct_map(county_json:dict, color_scheme, hover_data, feat_of_interest, alias):
    # Instantiate map object
    m = folium.Map(location=[37.0902, -95.7129], 
                tiles="cartodbpositron", 
                zoom_start=3)

    # Colorbar
    colormap = cm.linear.YlOrRd_09.scale(0, 1)
    colormap.caption = color_scheme.name
    m.add_child(colormap)

    # Create county-level visualization
    folium.TopoJson(
        data=json.loads(requests.get(county_json).text),
        object_path="objects.us_counties_20m",
        style_function=style_function 
    ).add_to(m)

    # Add hover attributes
    n = folium.features.GeoJson(
        data=hover_data.to_json(), 
        style_function=style_function_hover,
        control=False,
        highlight_function=highlight_function,
        tooltip=folium.features.GeoJsonTooltip(
            fields=['State 1( MA Bnchmk!C0039)', 
                    'County Name 1( MA Bnchmk!D0039)', 
                    feat_of_interest],
            aliases=['State: ', 
                    'County: ', 
                    alias],
            style=("background-color: white; \
                    color: #333333; \
                    font-family: arial; \
                    font-size: 12px; \
                    padding: 10px;") 
        )
    )

    # Add on the hover to the original map
    m.add_child(n)
    m.keep_in_front(n)
    return(m) 


The code below all creates parameters for data visualization, such as the hover and the highlighted data. 

Below, we're visualizing the Inpatient Facility Utility.

The object `m` is the folium object that has the mappings.

In [73]:
style_function_hover = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}

highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}
                                
color_df = make_colorscale_df(county_df, "All", "All", "Inpatient Facility Utilizers( MA Base!C0027)")
org_mco_df = make_filtered_df(county_df, "All", "All")

fulldf = create_overlay_data(geojson_df=geoJSON_df, 
                             bpt_df=org_mco_df, 
                             feat_of_interest='Inpatient Facility Utilizers( MA Base!C0027)')
m = construct_map(county_json=county_geo, color_scheme=color_df, hover_data=fulldf, feat_of_interest='Inpatient Facility Utilizers( MA Base!C0027)', alias='Inpatient Facility: ')
m

## Summary
  * This notebook provides a high-level overview of the BPT data and its structure
  * We provide a Python script (`bpt.py`) that allows the analyst to access the zipped data objects and read them into Pandas dataframes for downstream analyses.